## Module 1 Coding Assignment:Exploratory Data Analysis (EDA) of US stocks price data

We will explore the OHLCV daily bars of 1,000 US stocks.

1. **We will explore the OHLCV daily bars of 1,000 US stocks.**

**Solution**:
* pkl can serialize a very wide range of objects, not just text data.
* Quick & easy serialization, for example for pausing and resuming a long-running but simple script.
* Pandas vs Numpy Pandas has a better performance when number of rows is 500K or more. Indexing of numpy Arrays is very fast and computational process are fast with numpy. Thus when there exists some normal computations to do be does use numpy array while working with big Datasets generally as seen in most machine learning problems use dataframe.


2.	**Give an example of a dual class stock contained in the data.**

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
!pip install ydata-profiling #Replace pandas_profililng with ydata_profiling

In [ ]:
import pandas as pd
import numpy as np
import os
import datetime
import sys
from ydata_profiling import ProfileReport

In [ ]:
# Load data
daily_path = '/content/drive/MyDrive/Colab Notebooks/northwestern/R3K_Daily.bz2'
daily_df = pd.read_pickle(daily_path)
print(daily_df.shape)
daily_df.head()

(3894844, 8)


Date       Open       High        Low      Close  UnAdjustedClose  \
0 2000-12-01  33.287973  34.388402  33.170070  33.327274          53.0000   
1 2000-12-04  32.737759  33.366575  31.755233  32.069641          51.0000   
2 2000-12-05  33.170070  35.017219  33.052167  34.624208          55.0625   
3 2000-12-06  34.742111  35.803239  32.698458  32.698458          52.0000   
4 2000-12-07  33.012866  34.506305  32.305447  33.956091          54.0000   

  Volume Symbol  
0  36286      A  
1  28951      A  
2  54723      A  
3  43669      A  
4  30599      A

In [ ]:
# The dataset contains dual class stock with a period and then a class symbol after that.
symbols=daily_df.Symbol.unique()

In [ ]:
# Symbols containing a period
has_class=symbols[np.array([symbol.find(".") for symbol in symbols])>-1]
print(has_class)

['BF.A' 'BF.B' 'BRK.B' 'CRD.B' "FCE.A'" 'HEI.A' 'JW.A' 'LEN.B' 'MOG.A']


In [ ]:
# Those symbols with the period and class letter removed
without_class=np.unique(np.array([symbol.split('.')[0] for symbol in has_class]))
print(without_class)
print(without_class[np.in1d(without_class, symbols)])

['BF' 'BRK' 'CRD' 'FCE' 'HEI' 'JW' 'LEN' 'MOG']
['HEI' 'LEN']


**Solution**:
Some examples are (BF.A, BF.B), (BRK.A, BRK.B), (HEI, HEI.A)


3.	**Run profiling function. What is the Minimum Close price? Which stock does that belong to? Is it really possible to trade a stock that is worth less than a cent? If not, what isthe cause of such low prices?**


In [ ]:
ProfileReport(daily_df, title="Profiling Report")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

We find from the dataset that the minimum close price value is 0.00889341

In [ ]:
daily_df.loc[daily_df.Close==0.00889341]

Date      Open      High       Low     Close  UnAdjustedClose  \
3707037 2004-10-25  0.008893  0.008893  0.008893  0.008893             0.01   

        Volume Symbol  
3707037     11   WETF

**Solution**:
Minimum close Price : 0.00889341 which belongs to the stock with symbol "WETF"
Do stocks really trade for fractions of a penny? Sort of (reuters.com) http://blogs.reuters.com/ben-walsh/2013/11/18/do-stocks-really-trade-forfractions-of-a-penny-sort-of/ Split adjustment is one reason


4.	**What does “Rejected” mean next to the line “High is highly correlated with Close”?**

**Solution**:
Null Hypothesis: states that there is no effect or relationship between the variables. This Rejected signifies that the null hypothesis has been rejected which in turn means that the column “High is highly correlated with close”.
(Ref: Failing to Reject the Null Hypothesis - Statistics By Jim: https://statisticsbyjim.com/hypothesis-testing/failing-reject-null-hypothesis/)


5.	**Compare the price histories of KORS vs CPRI: do you notice anything strange? Read http://www.capriholdings.com/news-releases/news-releases-details/2018/Michael-KorsHoldings-Limited-to-Be-Renamed-Capri-Holdings-Limited/default.aspx and explain how you would handle these price histories.**




**Solution**:
We fill the dates where CRPI doesnt have a value. We find that there is only a single day with the given scenario so we fill that missing value by extracting that given date data from "KORS" and then discard the column of KORS since the company now no longer uses that symbol and trades with the CPRI symbol.


6.	Compare the price histories of GOOG vs GOOGL: do you notice anything strange? Read https://en.wikipedia.org/wiki/Alphabet_Inc. and explain how you would handle these price histories.

The data with the same unadjusted closes starts on the first day of data, is contiguous, and is immediately followed by the data with different unadjusted closes. The boundary is when the new class of non-voting shares GOOGL was introduced. It appears that someone has backfilled GOOGL (class C) to manufacture a record starting at the same time as GOOG (class A). It is definitely the case that the unadjusted prices (and everything else!) for GOOGL before 2014-03-27 are fiction, and therefore not point-in-time. The GOOG volume drops from over 51,000 to as low as 79 at the boundary, which could cause significant problems for strategies that use volume.
For GOOG and GOOGL the data with the same unadjusted closes starts on the first day of data, is contiguous, and is immediately followed by the data with different unadjusted closes. When new class of non voting shares GOOGL was introduced it seems GOOGL(C-class) was backfilled ot manufacture a record starting at the same time as GOOG(A-class). Thus the unadjusted prices for GOOGL before 2014-03-27 are backfilled ones and dont exist at that point. Also the GOOG volume drops from 51,000 to a value of 79 which coudl cause problems with strategies which are based on volume.

For GOOG, Yahoo! Finance charts show a 1000/2002 split on 2013-03-27 and a 1/1 split on 2015-04-27, and for GOOGL, a 1000/1998 split on 201404-03. At that point, we see the unadjusted closes for both are very similar.

Thus we could rather choose GOOGL because it seems to have no volume issues around the split.


7.	**Compare the price histories of GOV vs OPI: do you notice anything strange? Read https://www.businesswire.com/news/home/20181231005141/en/Government-PropertiesIncome-Trust-Announces-the-Completion-of-its-Merger-with-Select-Income-REIT and explain how you would handle these price histories.**

**Solution**:
 Government Properties Income Trust had completed its merger with Select Income REIT and thus changed the name to "Office Properties Income Trust” and started trading with the ticker OPI The Yahoo Finance shows a 4/1 split on 2019-01-2 for OPI. The particular event when this happened was during the ticker change. We should take OPI, discard GOV, and patch the 2018-12-5 prices of OPI with those of GOV on that date.

8.	**When you have a company that issues two classes of stocks (e.g. BF.A and BF.B), should you include both classes in your data? Discuss when you should, and should not.**

When there are two classes of stocks there comes an issue of replication of data which could overweight that particular stock and disguise our backtest showing twice the profit. Therefore we should generally try including the ones which have more datapoints(we can check which one has missing dates and such). There are also different parameters based on which we could identify which one we could keep and which we discard one of them is Volume parameter as this signifies which class of stock is more liquid. We can keep both classes of stocks if we want to get arbitrage in between them.(eg. British oil company Shell ). Thus if we want to check the possibility of a potential pair trading arbitrage condition we keep both the class

9.	**What is survivorship bias with respect to a stock database? If I claim that this dataset represents US stocks with the top 1,000 market capitalization, does it have survivorshipbias? Can you devise a simple method to find out?**

**Solution**:
In finance, survivorship bias is when studies on stock returns only use databases that contain data about companies that currently exist, and fail to include data about the ones that are no longer existing. The existence of Survivorship bias in data creates conclusions that are overly optimistic, and that may not be representative of real-life environments.
Enron - ENE Worldcom WCOM Lehman Brothers LEH (before going bankrupt used to be the fourth largest investment bank in US) Pets.com IPET
Toys-R-Us TOY
If it is stated that the dataset represents the top 1000 market capitlization companies then there is a chance the dataset will definetely miss out bankrupt companies thus showing survivorship bias.


In [ ]:
stock_symbol = daily_df.Symbol.unique()

In [ ]:
type(stock_symbol)

numpy.ndarray

In [ ]:
stock_symbol

array(['A', 'AAC', 'AAL', ..., 'ZAGG', 'ZEUS', 'ZIXI'], dtype=object)

In [ ]:
'LEH' in stock_symbol

False

This shows the dataset we used does not have the stock value of Lehman brothers which went bankrupt during the 2008 crisis.